In [91]:
import numpy as np # linear algebra
import pandas as pd 
import seaborn as sns
import plotly.express as px
import plotly.graph_objs as go
import plotly.offline as pyo
import xgboost as xgb
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split

In [47]:
df = pd.read_csv("train.csv")

In [48]:
df.head()

Id        AB          AF          AH         AM        AR  \
0  000ff2bfdfe9  0.209377  3109.03329   85.200147  22.394407  8.138688   
1  007255e47698  0.145282   978.76416   85.200147  36.968889  8.138688   
2  013f2bd269f5  0.470030  2635.10654   85.200147  32.360553  8.138688   
3  043ac50845d5  0.252107  3819.65177  120.201618  77.112203  8.138688   
4  044fb8a146ec  0.380297  3733.04844   85.200147  14.103738  8.138688   

         AX        AY         AZ          BC  ...        FL        FR  \
0  0.699861  0.025578   9.812214    5.555634  ...  7.298162   1.73855   
1  3.632190  0.025578  13.517790    1.229900  ...  0.173229   0.49706   
2  6.732840  0.025578  12.824570    1.229900  ...  7.709560   0.97556   
3  3.685344  0.025578  11.053708    1.229900  ...  6.122162   0.49706   
4  3.942255  0.054810   3.396778  102.151980  ...  8.153058  48.50134   

         FS         GB          GE            GF         GH         GI  \
0  0.094822  11.339138   72.611063   2003.810319  22.136229  69.834944   
1  0.568932   9.292698   72.611063  27981.562750  29.135430  32.131996   
2  1.198821  37.077772   88.609437  13676.957810  28.022851  35.192676   
3  0.284466  18.529584   82.416803   2094.262452  39.948656  90.493248   
4  0.121914  16.408728  146.109943   8524.370502  45.381316  36.262628   

          GL  Class  
0   0.120343      1  
1  21.978000      0  
2   0.196941      0  
3   0.155829      0  
4   0.096614      1  

[5 rows x 58 columns]

In [49]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 617 entries, 0 to 616
Data columns (total 58 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Id      617 non-null    object 
 1   AB      617 non-null    float64
 2   AF      617 non-null    float64
 3   AH      617 non-null    float64
 4   AM      617 non-null    float64
 5   AR      617 non-null    float64
 6   AX      617 non-null    float64
 7   AY      617 non-null    float64
 8   AZ      617 non-null    float64
 9   BC      617 non-null    float64
 10  BD      617 non-null    float64
 11  BN      617 non-null    float64
 12  BP      617 non-null    float64
 13  BQ      557 non-null    float64
 14  BR      617 non-null    float64
 15  BZ      617 non-null    float64
 16  CB      615 non-null    float64
 17  CC      614 non-null    float64
 18  CD      617 non-null    float64
 19  CF      617 non-null    float64
 20  CH      617 non-null    float64
 21  CL      617 non-null    float64
 22  CR

In [50]:
cols_list = df.columns.tolist()

## colunm name BD has space in it so I am removing that space

In [51]:
df = df.rename(columns={'BD ': 'BD'})

# I am going to fill missing values

In [52]:
fig = px.imshow(df.isnull(), color_continuous_scale='Viridis')
fig.update_layout(title='Missing Data Heatmap')
fig.update_xaxes(title='Columns')
fig.update_yaxes(title='Rows')
fig.show()

In [53]:
cols_list = df.columns.tolist()
cols_list = cols_list[1:-1]
for col in cols_list:
    if df[col].isna().sum() != 0:
        print(f"\'{col}\',", end="")

'BQ','CB','CC','DU','EL','FC','FL','FS','GL',

In [54]:
list_of_null = ['BQ','CB','CC','DU','EL','FC','FL','FS','GL']

## going to mean of the colum on missing data

In [55]:
for nullcol in list_of_null:
    print(nullcol)
    df[nullcol].fillna(df[nullcol].mean(), inplace=True)

BQ
CB
CC
DU
EL
FC
FL
FS
GL


In [56]:
fig = px.imshow(df.isnull(), color_continuous_scale='Viridis')
fig.update_layout(title='Missing Data Heatmap')
fig.update_xaxes(title='Columns')
fig.update_yaxes(title='Rows')
fig.show()

In [57]:
print(df.info())
df.head()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 617 entries, 0 to 616
Data columns (total 58 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Id      617 non-null    object 
 1   AB      617 non-null    float64
 2   AF      617 non-null    float64
 3   AH      617 non-null    float64
 4   AM      617 non-null    float64
 5   AR      617 non-null    float64
 6   AX      617 non-null    float64
 7   AY      617 non-null    float64
 8   AZ      617 non-null    float64
 9   BC      617 non-null    float64
 10  BD      617 non-null    float64
 11  BN      617 non-null    float64
 12  BP      617 non-null    float64
 13  BQ      617 non-null    float64
 14  BR      617 non-null    float64
 15  BZ      617 non-null    float64
 16  CB      617 non-null    float64
 17  CC      617 non-null    float64
 18  CD      617 non-null    float64
 19  CF      617 non-null    float64
 20  CH      617 non-null    float64
 21  CL      617 non-null    float64
 22  CR

Id        AB          AF          AH         AM        AR  \
0  000ff2bfdfe9  0.209377  3109.03329   85.200147  22.394407  8.138688   
1  007255e47698  0.145282   978.76416   85.200147  36.968889  8.138688   
2  013f2bd269f5  0.470030  2635.10654   85.200147  32.360553  8.138688   
3  043ac50845d5  0.252107  3819.65177  120.201618  77.112203  8.138688   
4  044fb8a146ec  0.380297  3733.04844   85.200147  14.103738  8.138688   

         AX        AY         AZ          BC  ...        FL        FR  \
0  0.699861  0.025578   9.812214    5.555634  ...  7.298162   1.73855   
1  3.632190  0.025578  13.517790    1.229900  ...  0.173229   0.49706   
2  6.732840  0.025578  12.824570    1.229900  ...  7.709560   0.97556   
3  3.685344  0.025578  11.053708    1.229900  ...  6.122162   0.49706   
4  3.942255  0.054810   3.396778  102.151980  ...  8.153058  48.50134   

         FS         GB          GE            GF         GH         GI  \
0  0.094822  11.339138   72.611063   2003.810319  22.136229  69.834944   
1  0.568932   9.292698   72.611063  27981.562750  29.135430  32.131996   
2  1.198821  37.077772   88.609437  13676.957810  28.022851  35.192676   
3  0.284466  18.529584   82.416803   2094.262452  39.948656  90.493248   
4  0.121914  16.408728  146.109943   8524.370502  45.381316  36.262628   

          GL  Class  
0   0.120343      1  
1  21.978000      0  
2   0.196941      0  
3   0.155829      0  
4   0.096614      1  

[5 rows x 58 columns]

### all missing values are fill and
# let check EJ colum which has datatype object

In [58]:
df["EJ"].unique()


array(['B', 'A'], dtype=object)

In [59]:
counts = df['EJ'].value_counts()

In [60]:
# Create the pie chart
fig = px.pie(counts, values=counts.values, names=counts.index)
fig.show()

In [61]:
fig = px.histogram(df, x="EJ")

# add title and axis labels
fig.update_layout(
    title="Distribution of EJ values",
    xaxis_title="EJ values",
    yaxis_title="Count"
)

# show chart
fig.show()

## I am going convert A and B to the one two 

In [62]:
# Define a dictionary to map categories to numerical values
mapping = {'A': 0, 'B': 1}

# Use the map() method to convert the 'EJ' column to numerical data
dfcon = df.copy()
dfcon['EJ'] = dfcon['EJ'].map(mapping)

# Print the updated DataFrame
print(dfcon['EJ'])

0      1
1      0
2      1
3      1
4      1
      ..
612    0
613    1
614    0
615    1
616    0
Name: EJ, Length: 617, dtype: int64


# here I am going to show box plot but we have lot of colum so I am going 10 by 10 colum


In [63]:
# firstlist = cols_list[]
fig = px.box(dfcon, y=cols_list[0:11])
fig.show()

In [64]:
# firstlist = cols_list[]
fig = px.box(dfcon, y=cols_list[12:23])
fig.show()

In [65]:
# firstlist = cols_list[]
fig = px.box(dfcon, y=cols_list[24:34])
fig.show()

In [66]:
fig = px.box(dfcon, y=cols_list[34:45])
fig.show()

In [67]:
fig = px.box(dfcon, y=cols_list[46:56])
fig.show()

## I am going to change the outline into nan

In [68]:
dfremove = dfcon.copy()

### converting outliner values into nan
#### I hand pick some outliner make them into nan and after that I will fill the values with mean of the col

In [69]:
outliers = dfremove[dfremove['AF'] > 14000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'AF'] = np.nan

# print the updated datafram

In [70]:
outliers = dfremove[dfremove['BD'] > 12000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'BD'] = np.nan

# print the updated datafram

In [71]:
outliers = dfremove[dfremove['BR'] > 10000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'BR'] = np.nan

# print the updated datafram

In [72]:
outliers = dfremove[dfremove['BZ'] > 40000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'BZ'] = np.nan

# print the updated datafram

In [73]:
outliers = dfremove[dfremove['EG'] > 10000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'EG'] = np.nan

# print the updated datafram

In [74]:
outliers = dfremove[dfremove['GF'] > 100000].index

# set the values of outliers to np.nan
dfremove.loc[outliers, 'GF'] = np.nan

# print the updated datafram

## Take a look  at missing values

In [75]:
fig = px.imshow(dfremove.isnull(), color_continuous_scale='Viridis')
fig.update_layout(title='Missing Data Heatmap')
fig.update_xaxes(title='Columns')
fig.update_yaxes(title='Rows')
fig.show()

In [76]:
cols_list = dfremove.columns.tolist()
cols_list = cols_list[1:-1]
for col in cols_list:
    if dfremove[col].isna().sum() != 0:
        print(f"\'{col}\',", end="")

'AF','BD','BR','BZ','EG','GF',

In [77]:
list_of_null =['AF','BD','BR','BZ','EG','GF']

In [78]:
for nullcol in list_of_null:
    print(nullcol)
    dfremove[nullcol].fillna(df[nullcol].mean(), inplace=True)

AF
BD
BR
BZ
EG
GF


In [79]:
fig = px.imshow(dfremove.isnull(), color_continuous_scale='Viridis')
fig.update_layout(title='Missing Data Heatmap')
fig.update_xaxes(title='Columns')
fig.update_yaxes(title='Rows')
fig.show()

In [80]:
dfremove['EJ'] = dfremove['EJ'].astype(float)

In [84]:
cols_list = dfremove.columns.tolist()
cols_list = cols_list[1:-1]


In [88]:
X = dfremove.loc[:, cols_list] # select the first and last columns
y = dfremove["Class"].astype(float)

In [89]:
y.info()

<class 'pandas.core.series.Series'>
RangeIndex: 617 entries, 0 to 616
Series name: Class
Non-Null Count  Dtype  
--------------  -----  
617 non-null    float64
dtypes: float64(1)
memory usage: 4.9 KB


In [93]:
# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

# Create XGBoost DMatrix
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test)

# Set XGBoost parameters
params = {'objective': 'binary:logistic',
          'max_depth': 3,
          'learning_rate': 0.1}

# Train the model
num_rounds = 50
xgb_model = xgb.train(params, dtrain, num_rounds)

# Make predictions on the testing data
y_pred = xgb_model.predict(dtest)
y_pred = [1 if p > 0.5 else 0 for p in y_pred]

# Calculate accuracy score
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)

Accuracy: 0.956989247311828


In [94]:
y_pred = xgb_model.predict(dtest)

In [96]:
dftest = pd.read_csv("test.csv")

In [104]:
# X_test
dftest.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5 entries, 0 to 4
Data columns (total 57 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   Id      5 non-null      object 
 1   AB      5 non-null      float64
 2   AF      5 non-null      float64
 3   AH      5 non-null      float64
 4   AM      5 non-null      float64
 5   AR      5 non-null      float64
 6   AX      5 non-null      float64
 7   AY      5 non-null      float64
 8   AZ      5 non-null      float64
 9   BC      5 non-null      float64
 10  BD      5 non-null      float64
 11  BN      5 non-null      float64
 12  BP      5 non-null      float64
 13  BQ      5 non-null      float64
 14  BR      5 non-null      float64
 15  BZ      5 non-null      float64
 16  CB      5 non-null      float64
 17  CC      5 non-null      float64
 18  CD      5 non-null      float64
 19  CF      5 non-null      float64
 20  CH      5 non-null      float64
 21  CL      5 non-null      float64
 22  CR    

In [101]:
# Define a dictionary to map categories to numerical values
mapping = {'A': 0, 'B': 1}

# Use the map() method to convert the 'EJ' column to numerical data

dftest['EJ'] = dftest['EJ'].map(mapping)
# Print the updated DataFrame

In [103]:
dftest['EJ'] = dftest['EJ'].astype(float)


In [105]:
dftest1 = dftest.copy()

In [106]:
dftest1 = dftest1.drop('Id', axis=1)

In [110]:
dftest1 = dftest1.rename(columns={'BD ': 'BD'})

In [111]:
dtest = xgb.DMatrix(dftest1)

In [112]:
pred = xgb_model.predict(dtest)

In [130]:
sub = dftest['Id']

In [131]:
sub1 = pd.DataFrame(sub, columns=['Id'])

In [133]:
sub1['class_1'] = pred

In [135]:
sub1['class_0'] = 1-sub1['class_1']

In [137]:
sub1.to_csv('submission.csv', index=False)

In [140]:
# # Define a dictionary to map categories to numerical values
# mapping = {'A': 0, 'B': 1}

# # Use the map() method to convert the 'EJ' column to numerical data

# dftest['EJ'] = dftest['EJ'].map(mapping)
# # Print the updated DataFrame
# dftest['EJ'] = dftest['EJ'].astype(float)
# dftest1 = dftest.copy()
# dftest1 = dftest1.drop('Id', axis=1)
# dftest1 = dftest1.rename(columns={'BD ': 'BD'})
# dtest = xgb.DMatrix(dftest1)
# pred = xgb_model.predict(dtest)
# sub = dftest['Id']
# sub1 = pd.DataFrame(sub, columns=['Id'])
# sub1['class_1'] = pred
# sub1['class_0'] = 1-sub1['class_1']

In [138]:
sub1 = sub1[['Id', 'class_0', 'class_1']]

In [139]:
sub1

Id  class_0  class_1
0  00eed32682bb  0.58681  0.41319
1  010ebe33f668  0.58681  0.41319
2  02fa521e1838  0.58681  0.41319
3  040e15f562a2  0.58681  0.41319
4  046e85c7cc7f  0.58681  0.41319